    "اول کلاس کد مربوط به بخش انکدر شبکه ماشین ترجمه عصبی است. همانطور که در فایل متنی به تفصیل ارائه شده است، انکدر یک شبکه عصبی دو طرفه ال اس تی ام است"


In [25]:
import sys
from chainer import *
from utilities import *
import random
import copy

class Encoder(Chain):
    #Bi-directional LSTM (forward + backward)
    def __init__(self, source_vocabulary_size, embed_size, hidden_size, source_vocabulary, source_word2vec, use_dropout, dropout_rate, library):
        super(Encoder, self).__init__(
            word2embed = links.EmbedID(source_vocabulary_size, embed_size, ignore_label = -1),
            embed2hidden_forward = links.LSTM(embed_size, hidden_size),
            embed2hidden_backward = links.LSTM(embed_size, hidden_size),
        )
        if source_word2vec is not None:
            for i in range(source_vocabulary_size):
                word = source_vocabulary.id2word[i]
                if word in source_word2vec:
                    self.word2embed.W.data[i] = source_word2vec[word]
        self.vocabulary_size = source_vocabulary_size
        self.embed_size = embed_size
        self.hidden_size = hidden_size
        self.use_dropout = use_dropout
        self.dropout_rate = dropout_rate
        self.library = library

    def __call__(self, sentence):
        return self.forward(sentence)[0]
    
    def forward(self, sentence):
        embed_states = list()
        hidden_backward_states = list()
        hidden_states = list()
        for word in sentence:
            embed_states.append(functions.dropout(functions.tanh(self.word2embed(word)), ratio = self.dropout_rate))
        for embed in embed_states[::-1]:
            hidden_backward_states.insert(0, functions.dropout(functions.tanh(self.embed2hidden_backward(embed)), ratio = 0.0)) #False
        for embed, hidden_backward in zip(embed_states, hidden_backward_states):
            plus = functions.dropout(functions.tanh(self.embed2hidden_forward(embed)), ratio = 0.0) + hidden_backward #False
            hidden_states.append(plus)
        return hidden_states, embed_states

    def reset_states(self):
        self.embed2hidden_forward.reset_state()
        self.embed2hidden_backward.reset_state()

    "کلاس بعدی اقدام به ایجاد شبکه دیکدر می نماید. شبکه دیکدر در نظر گرفته شده یک شبکه عصبی یک لایه یک طرفه ال اس تی ام است. همچنین برای بالا بردن دقت عملکردی برنامه به شبکه یک لایه اتنشن نیز اضافه شده است"


In [26]:
class Decoder(Chain):
	#Luong Global-Attention (dot)
    def __init__(self, target_vocabulary_size, embed_size, hidden_size, target_vocabulary, target_word2vec, use_dropout, dropout_rate, generation_limit, use_beamsearch, beam_size, library):
        super(Decoder, self).__init__(
            encoder2decoder_init = links.LSTM(hidden_size, hidden_size),
            word2embed = links.EmbedID(target_vocabulary_size, embed_size, ignore_label = -1),
            embed_hidden_tilde2hidden = links.LSTM(embed_size + hidden_size, hidden_size),
            attention_hidden2hidden_tilde = links.Linear(2 * hidden_size, hidden_size),
            hidden_tilde2predict = links.Linear(hidden_size, target_vocabulary_size),
        )
        if target_word2vec is not None:
            for i in range(target_vocabulary_size):
                word = target_vocabulary.id2word[i]
                if word in target_word2vec:
                    self.word2embed.W.data[i] = target_word2vec[word]
        self.vocabulary_size = target_vocabulary_size
        self.embed_size = embed_size
        self.hidden_size = hidden_size
        self.use_dropout = use_dropout
        self.dropout_rate = dropout_rate
        self.generation_limit = generation_limit
        self.use_beamsearch = use_beamsearch
        self.beam_size = beam_size
        self.library = library

    def __call__(self, encoder_hidden_states, sentence):
        return self.forward(encoder_hidden_states, sentence)[:2]

    def forward(self, encoder_hidden_states, sentence):
        predicts = list()
        target_embed_states = list()
        predict_embed_states = list()
        hidden_states = list()
        attention_weights_matrix = list()
        if sentence is not None:
            loss = Variable(self.library.zeros((), dtype = self.library.float32))
            for i, word in enumerate(sentence):
                if i == 0:
                    hidden = functions.dropout(functions.tanh(self.encoder2decoder_init(encoder_hidden_states[0])), ratio = 0.0) #False
                    encoder_hidden_states = functions.dstack(encoder_hidden_states)
                    self.copy_states()
                else:
                    previous_embed = functions.dropout(functions.tanh(self.word2embed(sentence[i - 1])), ratio = self.dropout_rate)
                    target_embed_states.append(previous_embed)
                    hidden = functions.dropout(functions.tanh(self.embed_hidden_tilde2hidden(functions.concat((previous_embed, hidden_tilde)))), ratio = 0.0) #False
                attention_weights = functions.softmax(functions.batch_matmul(encoder_hidden_states, hidden, transa = True))
                attention = functions.reshape(functions.batch_matmul(encoder_hidden_states, attention_weights), (encoder_hidden_states.shape[0], encoder_hidden_states.shape[1]))
                hidden_tilde = functions.dropout(functions.tanh(self.attention_hidden2hidden_tilde(functions.concat((attention, hidden)))), ratio = self.dropout_rate)
                hidden_states.append(hidden_tilde)
                score = self.hidden_tilde2predict(hidden_tilde)
                predict = functions.argmax(score, axis = 1)
                loss += functions.softmax_cross_entropy(score, word, ignore_label = -1)
                predict = functions.where(word.data == -1, word, predict)
                predicts.append(predict.data)
                predict_embed_states.append(functions.dropout(functions.tanh(self.word2embed(predict)), ratio = self.dropout_rate))
            target_embed_states.append(functions.dropout(functions.tanh(self.word2embed(sentence[-1])), ratio = self.dropout_rate))
            return loss, predicts, target_embed_states, predict_embed_states, hidden_states, None

        elif not self.use_beamsearch:
            while len(predicts) < self.generation_limit:
                if len(predicts) == 0:
                    hidden = functions.tanh(self.encoder2decoder_init(encoder_hidden_states[0]))
                    encoder_hidden_states = functions.dstack(encoder_hidden_states)
                    self.copy_states()
                else:
                    previous_embed = functions.tanh(self.word2embed(predict))
                    predict_embed_states.append(previous_embed)
                    hidden = functions.tanh(self.embed_hidden_tilde2hidden(functions.concat((previous_embed, hidden_tilde))))
                attention_weights = functions.softmax(functions.batch_matmul(encoder_hidden_states, hidden, transa = True))
                attention_weights_matrix.append(functions.reshape(attention_weights, (attention_weights.shape[0], attention_weights.shape[1])))
                attention = functions.reshape(functions.batch_matmul(encoder_hidden_states, attention_weights), (encoder_hidden_states.shape[0], encoder_hidden_states.shape[1]))
                hidden_tilde = functions.tanh(self.attention_hidden2hidden_tilde(functions.concat((attention, hidden))))
                hidden_states.append(hidden_tilde)
                score = self.hidden_tilde2predict(hidden_tilde)
                predict = functions.argmax(score, axis = 1)
                predicts.append(predict.data)
                if predict.data[0] == 1:
                    break
            predict_embed_states.append(functions.tanh(self.word2embed(predict)))
            attention_weights_matrix = functions.stack(attention_weights_matrix, axis = 1)
            return None, predicts, None, predict_embed_states, hidden_states, attention_weights_matrix

        else:
            initial_beam = [(0, None, list(), encoder_hidden_states, list(), list(), list())]
            for _, _, sentence, _, predict_embed_states, hidden_states, attention_weights_matrix in sorted(self.n_forwards(initial_beam), key = lambda x: x[0].data / len(x[2]), reverse = True):
                for word in sentence:
                    predicts.append(word.data)
                attention_weights_matrix = functions.stack(attention_weights_matrix, axis = 1)
                break
            return None, predicts, None, predict_embed_states, hidden_states, attention_weights_matrix

    def n_forwards(self, initial_beam):
        beam = [0] * self.generation_limit
        for i in range(self.generation_limit):
            beam[i] = list()
            if i == 0:
                new_beam = list()
                for logprob, states, sentence, encoder_hidden_states, embed_states, hidden_states, attention_weights_matrix in initial_beam:
                    hidden = functions.tanh(self.encoder2decoder_init(encoder_hidden_states[0]))
                    encoder_hidden_states = functions.dstack(encoder_hidden_states)
                    self.copy_states()
                    attention_weights = functions.softmax(functions.batch_matmul(encoder_hidden_states, hidden, transa = True))
                    attention = functions.reshape(functions.batch_matmul(encoder_hidden_states, attention_weights), (encoder_hidden_states.shape[0], encoder_hidden_states.shape[1]))
                    hidden_tilde = functions.tanh(self.attention_hidden2hidden_tilde(functions.concat((attention, hidden))))
                    prob = functions.softmax(self.hidden_tilde2predict(hidden_tilde))
                    cell, hidden = self.get_states()
                    for predict in numpy.argsort(cuda.to_cpu(prob.data)[0])[-1:-self.beam_size-1:-1]:
                        predict_variable = Variable(self.library.array([predict], dtype = self.library.int32))
                        if predict == 1:
                            new_beam.append((logprob + functions.log(prob[0][predict]), None, sentence + [predict_variable], encoder_hidden_states, embed_states + [functions.tanh(self.word2embed(predict_variable))], hidden_states + [hidden_tilde], attention_weights_matrix + [functions.reshape(attention_weights, (attention_weights.shape[0], attention_weights.shape[1]))])) 
                        else:
                            new_beam.append((logprob + functions.log(prob[0][predict]), (cell, hidden, hidden_tilde), sentence + [predict_variable], encoder_hidden_states, embed_states, hidden_states + [hidden_tilde], attention_weights_matrix + [functions.reshape(attention_weights, (attention_weights.shape[0], attention_weights.shape[1]))]))
                for _, (logprob, states, sentence, encoder_hidden_states, embed_states, hidden_states, attention_weights_matrix) in zip(range(self.beam_size), sorted(new_beam, key = lambda x: x[0].data / len(x[2]), reverse = True)):
                    beam[i].append((logprob, states, sentence, encoder_hidden_states, embed_states, hidden_states, attention_weights_matrix))
            else:
                new_beam = list()
                for logprob, states, sentence, encoder_hidden_states, embed_states, hidden_states, attention_weights_matrix in beam[i - 1]:
                    if states is not None:
                        previous_cell, previous_hidden, previous_hidden_tilde = states
                        self.embed_hidden_tilde2hidden.set_state(previous_cell, previous_hidden)
                        previous_embed = functions.tanh(self.word2embed(sentence[-1]))
                        hidden = functions.tanh(self.embed_hidden_tilde2hidden(functions.concat((previous_embed, previous_hidden_tilde))))
                        attention_weights = functions.softmax(functions.batch_matmul(encoder_hidden_states, hidden, transa = True))
                        attention = functions.reshape(functions.batch_matmul(encoder_hidden_states, attention_weights), (encoder_hidden_states.shape[0], encoder_hidden_states.shape[1]))
                        hidden_tilde = functions.tanh(self.attention_hidden2hidden_tilde(functions.concat((attention, hidden))))
                        prob = functions.softmax(self.hidden_tilde2predict(hidden_tilde))
                        cell, hidden = self.get_states()
                        for predict in numpy.argsort(cuda.to_cpu(prob.data)[0])[-1:-self.beam_size-1:-1]:
                            predict_variable = Variable(self.library.array([predict], dtype = self.library.int32))
                            if predict == 1:
                                new_beam.append((logprob + functions.log(prob[0][predict]), None, sentence + [predict_variable], encoder_hidden_states, embed_states + [previous_embed, functions.tanh(self.word2embed(predict_variable))], hidden_states + [hidden_tilde], attention_weights_matrix + [functions.reshape(attention_weights, (attention_weights.shape[0], attention_weights.shape[1]))])) 
                            else:
                                new_beam.append((logprob + functions.log(prob[0][predict]), (cell, hidden, hidden_tilde), sentence + [predict_variable], encoder_hidden_states, embed_states + [previous_embed], hidden_states + [hidden_tilde], attention_weights_matrix + [functions.reshape(attention_weights, (attention_weights.shape[0], attention_weights.shape[1]))]))
                    else:
                        new_beam.append((logprob, None, sentence, encoder_hidden_states, embed_states, hidden_states, attention_weights_matrix))
                for _, (logprob, states, sentence, encoder_hidden_states, embed_states, hidden_states, attention_weights_matrix) in zip(range(self.beam_size), sorted(new_beam, key = lambda x: x[0].data / len(x[2]), reverse = True)):
                    beam[i].append((logprob, states, sentence, encoder_hidden_states, embed_states, hidden_states, attention_weights_matrix))
        return beam[-1]


    def get_states(self):
        cell = copy.deepcopy(self.embed_hidden_tilde2hidden.c)
        hidden = copy.deepcopy(self.embed_hidden_tilde2hidden.h)
        return cell, hidden

    def copy_states(self):
        cell = self.encoder2decoder_init.c
        hidden = self.encoder2decoder_init.h
        self.embed_hidden_tilde2hidden.set_state(cell, hidden)

    def reset_states(self):
        self.encoder2decoder_init.reset_state()
        self.embed_hidden_tilde2hidden.reset_state()

    "کلاس زیر نیز به تعریف ماشین ترجمه عصبی مبتنی بر اتنشن می پردازد. برای تعیین وضعیت های مورد توجه مقادیر وضعیت ها از شبکه های انکدر و دیکدر دریافت می شود و با بررسی پیش بینی و خطای شبکه حالت ها مورد توجه برای شبکه تعیین می گردد"


In [27]:
class AttentionalNMT(Chain):
    def __init__(self, source_vocabulary_size, target_vocabulary_size, embed_size, hidden_size, source_vocabulary, target_vocabulary, source_word2vec, target_word2vec, use_dropout, dropout_rate, generation_limit, use_beamsearch, beam_size, library):
        super(AttentionalNMT, self).__init__(
            encoder = Encoder(source_vocabulary_size, embed_size, hidden_size, source_vocabulary, source_word2vec, use_dropout, dropout_rate, library),
            decoder = Decoder(target_vocabulary_size, embed_size, hidden_size, target_vocabulary, target_word2vec, use_dropout, dropout_rate, generation_limit, use_beamsearch, beam_size, library),
		)

    def __call__(self, batch_source, batch_target):
        self.reset_states()
        encoder_hidden_states = self.encoder(batch_source)
        loss, predicts = self.decoder(encoder_hidden_states, batch_target)
        return loss, predicts

    def forward(self, batch_source, batch_target):
        self.reset_states()
        encoder_hidden_states, source_embed_states = self.encoder.forward(batch_source)
        loss, predicts, target_embed_states, predict_embed_states, decoder_hidden_states, attention_matrix = self.decoder.forward(encoder_hidden_states, batch_target)
        return loss, predicts, source_embed_states, target_embed_states, predict_embed_states, encoder_hidden_states, decoder_hidden_states, attention_matrix
    
    def reset_states(self):
        self.encoder.reset_states()
        self.decoder.reset_states()

    "تابع زیر اقدام به استخراج کانفیگ های تعریف شده برای پارامترهای شبکه ماشین ترجمه عصبی می نماید. همچنین فایل های مرتبط برای برنامه شامل فایل لغات، بردارهای جاسازی لازم ساخته و یا بارگزاری می شود. در نهایت خروجی شبکه شامل خطا، مدل، وزن و مدل بهینه شبکه ذخیره می شود"


In [28]:
def train(config):
    if len(sys.argv) == 4:
        start = int(sys.argv[3]) - 1
        trace("Start Re-Training ...")
        trace("Loading Vocabulary ...")
        source_vocabulary = Vocabulary.load("{}.{:03d}.source_vocabulary".format(config.model, start))
        target_vocabulary = Vocabulary.load("{}.{:03d}.target_vocabulary".format(config.model, start))
        source_word2vec = None
        target_word2vec = None
    else:
        start = 0
        trace("Start Training ...")
        trace("Making Vocabulary ...")
        source_vocabulary = Vocabulary.make(config.source_train, config.source_vocabulary_size)
        target_vocabulary = Vocabulary.make(config.target_train, config.target_vocabulary_size)

        if config.use_word2vec == "Load":
            trace("Loading Word2vec ...")
            source_word2vec = load_word2vec(config.source_word2vec_file)
            target_word2vec = load_word2vec(config.target_word2vec_file)
            save_word2vec(source_word2vec, "{}.source_word2vec".format(config.model))
            save_word2vec(target_word2vec, "{}.target_word2vec".format(config.model))
        elif config.use_word2vec == "Make":
            trace("Making Word2vec ...")
            source_word2vec = make_word2vec(config.source_train, config.embed_size)
            target_word2vec = make_word2vec(config.target_train, config.embed_size)
            save_word2vec(source_word2vec, "{}.source_word2vec".format(config.model))
            save_word2vec(target_word2vec, "{}.target_word2vec".format(config.model))
        else:
            source_word2vec = None
            target_word2vec = None

    config.source_vocabulary_size = source_vocabulary.size
    config.target_vocabulary_size = target_vocabulary.size
    
    trace("Making Model ...")
    nmt = AttentionalNMT(config.source_vocabulary_size, config.target_vocabulary_size, config.embed_size, config.hidden_size, source_vocabulary, target_vocabulary, source_word2vec, target_word2vec, config.use_dropout, config.dropout_rate, None, False, None, config.library)
    if config.use_gpu:
        cuda.get_device(config.gpu_device).use()
        nmt.to_gpu()

    opt = config.optimizer
    opt.setup(nmt)
    opt.add_hook(optimizer.GradientClipping(5))


    if start != 0:
        serializers.load_hdf5("{}.{:03d}.weights".format(config.model, start), nmt)
        serializers.load_hdf5("{}.{:03d}.optimizer".format(config.model, start), opt)

    for epoch in range(start, config.epoch):
        trace("Epoch {}/{}".format(epoch + 1, config.epoch))
        accum_loss = 0.0
        finished = 0
        random.seed(epoch)
        for batch_source, batch_target in random_sorted_parallel_batch(config.source_train, config.target_train, source_vocabulary, target_vocabulary, config.batch_size, config.pooling, config.library):
            nmt.zerograds()
            loss, batch_predict = nmt(batch_source, batch_target)
            accum_loss += loss.data
            loss.backward()
            opt.update()

            for source, target, predict in zip(convert_wordlist(batch_source, source_vocabulary), convert_wordlist(batch_target, target_vocabulary), convert_wordlist(batch_predict, target_vocabulary)):
                trace("Epoch {}/{}, Sample {}".format(epoch + 1, config.epoch, finished + 1))
                trace("Source  = {}".format(source))
                trace("Target  = {}".format(target))
                trace("Predict = {}".format(predict))
                finished += 1

        trace("accum_loss = {}".format(accum_loss))
        trace("Saving Model ...")
        model = "{}.{:03d}".format(config.model, epoch + 1)
        source_vocabulary.save("{}.source_vocabulary".format(model))
        target_vocabulary.save("{}.target_vocabulary".format(model))
        serializers.save_hdf5("{}.weights".format(model), nmt)
        serializers.save_hdf5("{}.optimizer".format(model), opt)

    trace("Finished.")

    "در صورتی که قصد تست شبکه را داشته باشیم تابع زیر فراخوانی می شود. با توجه به تابع مقادیر پارامترهای متناسب و کلمات ورودی و خروجی شبکه خواهنده شده. ترجمه شبکه تهیه می شود و مقدار خطای شبکه با توحه به مقدار پارامتر جستجو مشخص می گردد"


In [29]:
def test(config):
    trace("Loading Vocabulary ...")
    source_vocabulary = Vocabulary.load("{}.source_vocabulary".format(config.model))
    target_vocabulary = Vocabulary.load("{}.target_vocabulary".format(config.model))
    config.source_vocabulary_size = source_vocabulary.size
    config.target_vocabulary_size = target_vocabulary.size

    trace("Loading Model ...")
    nmt = AttentionalNMT(config.source_vocabulary_size, config.target_vocabulary_size, config.embed_size, config.hidden_size, source_vocabulary, target_vocabulary, None, None, False, 0.0, config.generation_limit, config.use_beamsearch, config.beam_size, config.library)
    if config.use_gpu:
        cuda.get_device(config.gpu_device).use()
        nmt.to_gpu()
    serializers.load_hdf5("{}.weights".format(config.model), nmt)

    trace("Generating Translation ...")
    finished = 0
    
    with open(config.predict_file, 'w') as ft:
        for batch_source in mono_batch(config.source_file, source_vocabulary, 1, config.library):
            trace("Sample {} ...".format(finished + 1))
            _, batch_predict, _, _, _, _, _, batch_attention = nmt.forward(batch_source, None)
            for source, predict, attention in zip(convert_wordlist(batch_source, source_vocabulary), convert_wordlist(batch_predict, target_vocabulary), batch_attention.data):
                ft.write("{}\n".format(predict))
                finished += 1



in below part: we havd two parameters. 
    argv1: define mode of run, you can use one of these modes: 'train' , 'dev' , 'test'
    argv2: define path of config file. this file contains all parameters value and dataset address (the path is important and must be check based on you system location)

In [30]:
if __name__ == "__main__":
    sys.argv[1] = 'train'
    sys.argv[2] = '/home/alireza/Downloads/pycharm-community-2017.2.4/bin/GAN-NMT_master/sample/sample_gan.config'
    config = Configuration(sys.argv[1], sys.argv[2])
    if config.mode == "train":
        train(config)
    elif config.mode == "test":
        trace("Start Testing ...")
        config.source_file = config.source_test
        config.predict_file = "{}.test_result.beam{}".format(config.model, config.beam_size)
        config.model = "{}.{:03d}".format(config.model, int(sys.argv[3]))
        test(config)
        trace("Finished.")
    elif config.mode == "dev":
        trace("Start Developing ...")
        config.source_file = config.source_dev
        model = config.model
        if len(sys.argv) == 5:
            start = int(sys.argv[3]) - 1
            end = int(sys.argv[4])
        else:
            start = 0
            end = config.epoch
        for i in range(start, end):
            config.model = "{}.{:03d}".format(model, i + 1)
            trace("Model {}/{}".format(i + 1, config.epoch))
            config.predict_file = "{}.dev_result".format(config.model)
            test(config)
        trace("Finished.")

2019-10-17 07:57:57.458522 ... Start Training ...
2019-10-17 07:57:57.459204 ... Making Vocabulary ...
2019-10-17 07:57:57.637930 ... Making Word2vec ...
2019-10-17 07:57:59.147552 ... Making Model ...
/usr/local/lib/python3.6/dist-packages/ipykernel_launcher.py:18: DeprecationWarning: Call to deprecated `__contains__` (Method will be removed in 4.0.0, use self.wv.__contains__() instead).
/usr/local/lib/python3.6/dist-packages/ipykernel_launcher.py:19: DeprecationWarning: Call to deprecated `__getitem__` (Method will be removed in 4.0.0, use self.wv.__getitem__() instead).
/usr/local/lib/python3.6/dist-packages/ipykernel_launcher.py:14: DeprecationWarning: Call to deprecated `__contains__` (Method will be removed in 4.0.0, use self.wv.__contains__() instead).
  
/usr/local/lib/python3.6/dist-packages/ipykernel_launcher.py:15: DeprecationWarning: Call to deprecated `__getitem__` (Method will be removed in 4.0.0, use self.wv.__getitem__() instead).
  from ipykernel import kernelapp as ap

2019-10-17 07:58:03.895530 ... Predict = piano piano piano piano piano piano piano piano piano piano bazaar bazaar     
2019-10-17 07:58:03.896228 ... Epoch 1/3, Sample 23
2019-10-17 07:58:03.896752 ... Source  = 彼女 は 試験 に 失敗 し な い よう に 一生 懸命 勉強 し た 。
2019-10-17 07:58:03.897212 ... Target  = she studied hard lest she should fail in the exam .
2019-10-17 07:58:03.897767 ... Predict = piano piano piano piano piano piano piano piano piano piano piano piano     
2019-10-17 07:58:03.898513 ... Epoch 1/3, Sample 24
2019-10-17 07:58:03.899017 ... Source  = 彼女 は その 金 が なくな っ て い る こと に 気付 い た 。
2019-10-17 07:58:03.899583 ... Target  = she found the money gone .
2019-10-17 07:58:03.900080 ... Predict = piano piano piano piano piano piano piano          
2019-10-17 07:58:03.915291 ... Epoch 1/3, Sample 25
2019-10-17 07:58:03.915801 ... Source  = この 国 で は 、 ラクダ は な く て は な ら な い 。
2019-10-17 07:58:03.916846 ... Target  = they cannot do without camels in this country .
2019-10-17 07:58:03.917303 .

2019-10-17 07:58:04.022104 ... Target  = with all her faults , i still like her .
2019-10-17 07:58:04.022642 ... Predict = piano piano piano piano piano piano piano piano piano piano piano      
2019-10-17 07:58:04.023401 ... Epoch 1/3, Sample 49
2019-10-17 07:58:04.023849 ... Source  = 年老い た スミス さん は 出来 る だけ お 金 を ため て い る 。
2019-10-17 07:58:04.025094 ... Target  = old mr smith is saving as much money as he can .
2019-10-17 07:58:04.025722 ... Predict = piano piano piano piano piano piano piano piano piano piano piano piano thoughtless    
2019-10-17 07:58:04.026356 ... Epoch 1/3, Sample 50
2019-10-17 07:58:04.027087 ... Source  = あなた が 私 の 立場 に い たら 、 何 を し ま す か 。
2019-10-17 07:58:04.027546 ... Target  = what would you do , if you were in my place ?
2019-10-17 07:58:04.028202 ... Predict = piano piano piano piano piano piano piano piano piano piano thoughtless thoughtless thoughtless    
2019-10-17 07:58:04.029030 ... Epoch 1/3, Sample 51
2019-10-17 07:58:04.029670 ... Source  = 彼 の

2019-10-17 07:58:04.119004 ... Target  = do you know what he said ?
2019-10-17 07:58:04.119538 ... Predict = piano piano piano piano piano piano piano piano         
2019-10-17 07:58:04.120224 ... Epoch 1/3, Sample 74
2019-10-17 07:58:04.121520 ... Source  = 今 まで の ところ 彼 は 学校 で は 仲良く や っ て い る 。
2019-10-17 07:58:04.122125 ... Target  = so far he has done very well at school .
2019-10-17 07:58:04.122694 ... Predict = piano piano piano piano piano piano piano piano piano piano piano      
2019-10-17 07:58:04.123441 ... Epoch 1/3, Sample 75
2019-10-17 07:58:04.123901 ... Source  = 万一 明日 雨 が 降 っ たら 、 私 たち は バス で 行 く 。
2019-10-17 07:58:04.124618 ... Target  = if it should rain tomorrow , we would go by bus .
2019-10-17 07:58:04.125059 ... Predict = piano piano piano piano piano piano piano piano piano piano piano thoughtless thoughtless    
2019-10-17 07:58:04.125945 ... Epoch 1/3, Sample 76
2019-10-17 07:58:04.126387 ... Source  = 話し手 は 自分 の 言 う こと を 聞 い て もらえ な かっ た 。
2019-10-17 07:58:04.

2019-10-17 07:58:04.230520 ... Source  = あきらめ た 方 が 良 い の で は な い で しょ う か 。
2019-10-17 07:58:04.230991 ... Target  = you may as well give up .
2019-10-17 07:58:04.233620 ... Predict = piano piano piano piano piano piano piano piano         
2019-10-17 07:58:04.236017 ... Epoch 1/3, Sample 99
2019-10-17 07:58:04.236478 ... Source  = あの 珍本 を どう や っ て 手 に 入れ た の で す か 。
2019-10-17 07:58:04.237468 ... Target  = how did you come by those rare books ?
2019-10-17 07:58:04.238035 ... Predict = piano piano piano piano piano piano piano piano piano piano       
2019-10-17 07:58:04.238742 ... Epoch 1/3, Sample 100
2019-10-17 07:58:04.239214 ... Source  = 君 か 僕 が 選 ば れ る こと に な る で しょ う 。
2019-10-17 07:58:04.239638 ... Target  = you or i will be chosen .
2019-10-17 07:58:04.240051 ... Predict = piano piano piano piano piano piano piano piano         
2019-10-17 07:58:04.240709 ... Epoch 1/3, Sample 101
2019-10-17 07:58:04.242639 ... Source  = 何 か お 役 に 立 つ こと は ござ い ま せ ん か 。
2019-10-17 07:58:04.

...

2019-10-17 08:05:01.133779 ... Source  = 私 は 喜 ん で あなた の お 供 を し ま す 。
2019-10-17 08:05:01.134198 ... Target  = i am ready to follow you .
2019-10-17 08:05:01.134622 ... Predict = i have a . the . .
2019-10-17 08:05:01.135329 ... Epoch 3/3, Sample 4857
2019-10-17 08:05:01.135767 ... Source  = 彼 は あの 車 に 一 万 ドル 以上 かけ て い た 。
2019-10-17 08:05:01.136259 ... Target  = his car cost him upward of ten thousand dollars .
2019-10-17 08:05:01.136677 ... Predict = he have is . . . the . . .
2019-10-17 08:05:01.137312 ... Epoch 3/3, Sample 4858
2019-10-17 08:05:01.137837 ... Source  = 彼 は それ 以来 １ 度 も 戻 っ て こ な い 。
2019-10-17 08:05:01.138265 ... Target  = never has he returned since .
2019-10-17 08:05:01.138754 ... Predict = he is a . . .
2019-10-17 08:05:01.139440 ... Epoch 3/3, Sample 4859
2019-10-17 08:05:01.139909 ... Source  = 子供 が 生まれ て から めった に 彼 ら は 出かけ な い 。
2019-10-17 08:05:01.140362 ... Target  = they have scarcely gone out since the baby was born .
2019-10-17 08:05:01.141309 ... Predict

2019-10-17 08:05:04.651642 ... Predict = i have a to
2019-10-17 08:05:04.652740 ... Epoch 3/3, Sample 4887
2019-10-17 08:05:04.656316 ... Source  = 大変 悲し い こと に 父 は 若 く し て 亡くな っ た 。
2019-10-17 08:05:04.656765 ... Target  = to my great sorrow , my father died young .
2019-10-17 08:05:04.659845 ... Predict = i have a a . the
2019-10-17 08:05:04.661388 ... Epoch 3/3, Sample 4888
2019-10-17 08:05:04.661937 ... Source  = ぼく は もう 何 年 も テニス を や っ て い な い 。
2019-10-17 08:05:04.662410 ... Target  = i haven 't touched a tennis racket in years .
2019-10-17 08:05:04.662935 ... Predict = i have 't a .
2019-10-17 08:05:04.663608 ... Epoch 3/3, Sample 4889
2019-10-17 08:05:04.664159 ... Source  = 彼 は コンピューター の 使 い 方 を よく 知 っ て い る 。
2019-10-17 08:05:04.664621 ... Target  = he knows well how to use a computer .
2019-10-17 08:05:04.665147 ... Predict = he is a to the the .
2019-10-17 08:05:04.665816 ... Epoch 3/3, Sample 4890
2019-10-17 08:05:04.666301 ... Source  = 私 たち は 子供 の 幸福 の ため に あらゆる こと を し た

2019-10-17 08:05:04.766412 ... Source  = 私 たち の 学校 の 図書 館 に は 本 が たくさん あ る 。
2019-10-17 08:05:04.767514 ... Target  = our school library has many books .
2019-10-17 08:05:04.768004 ... Predict = i have is to the book .
2019-10-17 08:05:04.768665 ... Epoch 3/3, Sample 4918
2019-10-17 08:05:04.769124 ... Source  = 私 は 彼 が 正直 で あ る と 信 じ て い る 。
2019-10-17 08:05:04.769558 ... Target  = i believe that he is honest .
2019-10-17 08:05:04.770056 ... Predict = i have a a . the .
2019-10-17 08:05:04.770777 ... Epoch 3/3, Sample 4919
2019-10-17 08:05:04.771275 ... Source  = これ は 今 まで に 見 た 中 で もっとも 美し い 光景 だ 。
2019-10-17 08:05:04.775168 ... Target  = this is the most beautiful sight that i have ever seen .
2019-10-17 08:05:04.775562 ... Predict = i have is a a . . the . . . .
2019-10-17 08:05:04.776372 ... Epoch 3/3, Sample 4920
2019-10-17 08:05:04.777696 ... Source  = 私 は ８ 時 に きみ の 家 に い る だ ろ う 。
2019-10-17 08:05:04.778138 ... Target  = i will be at your house at eight .
2019-10-17 08:05:04.7

2019-10-17 08:05:04.869277 ... Source  = イギリス 人 なら もっと 違 っ た 行動 を と る だ ろ う 。
2019-10-17 08:05:04.869727 ... Target  = an englishman would act in a different way .
2019-10-17 08:05:04.870197 ... Predict = i have is a . the
2019-10-17 08:05:04.870859 ... Epoch 3/3, Sample 4948
2019-10-17 08:05:04.871356 ... Source  = この 映画 は とても おもしろ い と い う こと が 分か っ た 。
2019-10-17 08:05:04.871802 ... Target  = i found this film very interesting .
2019-10-17 08:05:04.872299 ... Predict = i have a a . the .
2019-10-17 08:05:04.879203 ... Epoch 3/3, Sample 4949
2019-10-17 08:05:04.879702 ... Source  = す み ま せ ん が 、 図書 館 は どこ で す か 。
2019-10-17 08:05:04.880187 ... Target  = excuse me , but where is the library ?
2019-10-17 08:05:04.880663 ... Predict = i is is a a . the
2019-10-17 08:05:04.881328 ... Epoch 3/3, Sample 4950
2019-10-17 08:05:04.881817 ... Source  = どちら の 道 を 行 っ て も かか る 時間 は 同じ だ 。
2019-10-17 08:05:04.882281 ... Target  = whichever way you take , it 'll take you the same time .
2019-10-17 

2019-10-17 08:05:04.975989 ... Source  = 部屋 は 白 い 服 を 着 た 女の子 で いっぱい で し た 。
2019-10-17 08:05:04.976457 ... Target  = the room was full of girls in white .
2019-10-17 08:05:04.976944 ... Predict = i have is a . the . the .
2019-10-17 08:05:04.977613 ... Epoch 3/3, Sample 4978
2019-10-17 08:05:04.978084 ... Source  = 明日 その こと に つ い て 彼 に 尋ね る つもり で す 。
2019-10-17 08:05:04.978550 ... Target  = i will ask him about it tomorrow .
2019-10-17 08:05:04.979041 ... Predict = i have a to . ? . .
2019-10-17 08:05:04.979699 ... Epoch 3/3, Sample 4979
2019-10-17 08:05:04.980171 ... Source  = 私 たち は そこ で 何 匹 か の 大きな 魚 を 捕まえ た 。
2019-10-17 08:05:04.980631 ... Target  = we caught some large fish there .
2019-10-17 08:05:04.981099 ... Predict = i is a a a . .
2019-10-17 08:05:04.981765 ... Epoch 3/3, Sample 4980
2019-10-17 08:05:04.982241 ... Source  = 私 たち は 子供 たち を 静か に さ せ て お い た 。
2019-10-17 08:05:04.982713 ... Target  = we kept the children quiet .
2019-10-17 08:05:04.983182 ... Predict = i is a


    "در ادامه نمونه از خروجی شبکه بر روی داده ای محدود از ترجمه زبان انگلیسی به ژاپنی را مشاهده می نماییم. خروجی زیر مربوط به زمانی است که قصد آموزش شبکه ماشین ترجمه عصبی را داشته ایم. خروجی حاصل مربوط به دور 3 اجرا و در بخش انتهایی از مرحله آموزش است."
